In [1]:
from diodem import load_data
from diodem.benchmark._benchmark import _max_coords_after_omc_pos_offset, _load_sys
import ring
import numpy as np
import qmt
import imt
import mediapy

In [2]:
solver = imt.Solver([-1, 0, 1, 0, 3], methods=None, Ts=0.01)

In [3]:
sys_str = """
<x_xy model="gait">
    <options gravity="0 0 9.81" dt="0.01"/>
    <worldbody>
        <body name="seg2" joint="free" damping="5 5 5 25 25 25">
            <omc name="seg2" pos_marker="2" pos="0 0 -.02"/>
            <geom type="box" mass="1" pos="0.1 0 0" dim="0.2 0.05 0.05" color="dustin_exp_white"/>
            <geom type="box" mass="0.1" pos="0.03 -0.05 0" dim="0.01 0.1 0.01" color="dustin_exp_white"/>
            <geom type="box" mass="0.1" pos="0.17 -0.05 0" dim="0.01 0.1 0.01" color="dustin_exp_white"/>
            <body name="imu2" joint="frozen" pos="0.1 0.0 0.035">
                <omc name="seg2" pos_marker="2" pos=".1 0 .015"/>
                <geom type="box" mass="0.1" dim="0.05 0.03 0.02" color="dustin_exp_orange"/>
            </body>
            <body name="seg1" joint="saddle" damping="3 3">
                <omc name="seg1" pos_marker="2" pos=".15 0 -.02"/>
                <geom type="box" mass="1" pos="-0.1 0 0" dim="0.2 0.05 0.05" color="dustin_exp_blue"/>
                <geom type="box" mass="0.1" pos="-0.03 -0.05 0" dim="0.01 0.1 0.01" color="dustin_exp_white"/>
                <geom type="box" mass="0.1" pos="-0.17 0.05 0" dim="0.01 0.1 0.01" color="dustin_exp_white"/>
                <body name="imu1" joint="frozen" pos="-0.1 0.0 0.035">
                    <omc name="seg1" pos_marker="2" pos=".05 0 .015"/>
                    <geom type="box" mass="0.1" dim="0.05 0.03 0.02" color="dustin_exp_orange"/>
                </body>
                <body name="seg5" joint="ry" pos="-0.2 0 0" damping="3">
                    <omc name="seg5" pos_marker="4" pos="0.15 0 -.02"/>
                    <geom type="box" mass="1" pos="-0.1 0 0" dim="0.2 0.05 0.05" color="dustin_exp_white"/>
                    <geom type="box" mass="0.1" pos="-0.03 -0.05 0" dim="0.01 0.1 0.01" color="black"/>
                    <geom type="box" mass="0.1" pos="-0.17 -0.05 0" dim="0.01 0.1 0.01" color="black"/>
                    <body name="imu5" joint="frozen" pos="-0.1 0.0 0.035">
                        <omc name="seg5" pos_marker="4" pos=".05 0 .015"/>
                        <geom type="box" mass="0.1" dim="0.05 0.03 0.02" color="dustin_exp_orange"/>
                    </body>
                </body>
            </body>
            <body name="seg3" joint="saddle" pos="0.2 0 0" damping="3 3">
                <omc name="seg3" pos_marker="1" pos="0 0 -.02"/>
                <geom type="box" mass="1" pos="0.1 0 0" dim="0.2 0.05 0.05" color="dustin_exp_blue"/>
                <geom type="box" mass="0.1" pos="0.05 0.05 0" dim="0.01 0.1 0.01" color="black"/>
                <geom type="box" mass="0.1" pos="0.15 -0.05 0" dim="0.01 0.1 0.01" color="black"/>
                <body name="imu3" joint="frozen" pos="0.1 0.0 0.035">
                    <omc name="seg3" pos_marker="1" pos=".1 0 .015"/>
                    <geom type="box" mass="0.1" dim="0.05 0.03 0.02" color="dustin_exp_orange"/>
                </body>
                <body name="seg4" joint="ry" pos="0.2 0 0" damping="3">
                    <omc name="seg4" pos_marker="2" pos="0 0 -.02"/>
                    <geom type="box" mass="1" pos="0.1 0 0" dim="0.2 0.05 0.05" color="dustin_exp_white"/>
                    <geom type="box" mass="0.1" pos="0.1 0.05 0" dim="0.01 0.1 0.01" color="black"/>
                    <geom type="box" mass="0.1" pos="0.15 -0.05 0" dim="0.01 0.1 0.01" color="black"/>
                    <body name="imu4" joint="frozen" pos="0.1 0.0 0.035">
                        <omc name="seg4" pos_marker="2" pos=".1 0 .015"/>
                        <geom type="box" mass="0.1" dim="0.05 0.03 0.02" color="dustin_exp_orange"/>
                    </body>
                </body>
            </body>
        </body>
    </worldbody>
</x_xy>
"""

In [4]:
exp_id = 10
motion = "gait_slow"
data = load_data(exp_id, motion)
sys = ring.System.create(sys_str)
max_coords = _max_coords_after_omc_pos_offset(sys, data)
xs = ring.sim2real.xs_from_raw(
    sys,
    max_coords,
    qinv=True,
)

In [5]:
imu_data = {
    i: dict(acc=data[seg]["imu_rigid"]["acc"], gyr=data[seg]["imu_rigid"]["gyr"]) for i, seg in enumerate(sys.findall_segments())
}

In [6]:
yhat, _ = solver.step(imu_data)

In [7]:
sys_noimu = sys.make_sys_noimu()[0]
y = ring.algorithms.sensors.rel_pose(sys_noimu, xs, sys)

In [8]:
yhat_child_to_parent = {
    'seg2': qmt.qinv(data['seg2']['quat']),
    'seg1': qmt.qmult(qmt.qinv(yhat[0]), yhat[1]),
    'seg5': qmt.qmult(qmt.qinv(yhat[1]), yhat[2]),
    'seg3': qmt.qmult(qmt.qinv(yhat[0]), yhat[3]),
    'seg4': qmt.qmult(qmt.qinv(yhat[3]), yhat[4]),
}

In [9]:
for seg in ['seg1', 'seg5', 'seg3', 'seg4']:
    print(np.mean(np.rad2deg(ring.maths.angle_error(y[seg], yhat_child_to_parent[seg]))[500:]))

7.640054
2.993848
5.214331
3.3962598


In [10]:
mediapy.show_video(sys.render_prediction(xs, yhat_child_to_parent, transparent_segment_to_root=False, render_every_nth=4, width=1280, height=720, camera="target", offset_pred=[0.5, 0, 0]), fps=25)

Rendering frames..: 100%|██████████| 1625/1625 [00:13<00:00, 120.80it/s]


This browser does not support the video tag.
